# Deep Learning Project - Emotion Classification

This notebook implements a **multi-label emotion classification system** using state-of-the-art transformer models. The goal is to predict multiple emotions (anger, fear, joy, sadness, surprise) that may be present in a given text.

**Key Features:**
- **Model**: Microsoft DeBERTa-v3-base (184M parameters)
- **Strategy**: 5-Fold Stratified Cross-Validation for robust performance estimation
- **Optimization**: Mixed Precision Training, Gradient Clipping, Learning Rate Warmup
- **Evaluation**: Macro F1 Score with Per-Label Threshold Tuning
- **Ensemble**: Average predictions across all folds for final submission

**Problem Type**: Multi-label classification (each text can have 0 or more emotions)

---

## 1. Imports & Setup

We import all necessary libraries for:
- **Data handling**: `numpy`, `pandas` for data manipulation
- **Deep learning**: `torch` (PyTorch) and `transformers` (Hugging Face) for model training
- **Evaluation**: `sklearn` for F1 metrics and stratified k-fold cross-validation
- **Optimization**: Mixed precision training with `autocast` and `GradScaler` to speed up training and reduce memory usage
- **Memory management**: `gc` for garbage collection to free up GPU memory between folds

In [ ]:
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import f1_score
from transformers import (
    AutoTokenizer,
    AutoModelForSequenceClassification,
    get_linear_schedule_with_warmup,
    AutoConfig
)
from torch.optim import AdamW
from torch.cuda.amp import autocast, GradScaler
import gc
import warnings
import os

warnings.filterwarnings("ignore")

## 2. Configuration

Centralized configuration class containing all hyperparameters and paths. This makes it easy to:
- Experiment with different settings
- Ensure reproducibility
- Keep the code organized

**Key Hyperparameters:**
- `MODEL_NAME`: DeBERTa-v3-base chosen for its strong performance on text classification tasks
- `MAX_LEN=128`: Balance between capturing context and computational efficiency
- `BATCH_SIZE=16`: Fits in GPU memory while maintaining good gradient estimates
- `LR=1.5e-5`: Small learning rate typical for fine-tuning pre-trained transformers
- `EPOCHS=4`: Sufficient for fine-tuning without overfitting
- `N_FOLDS=5`: Standard choice for cross-validation, balances between training data and validation reliability

In [ ]:
# ========= CONFIG =========
class Config:
    SEED = 42
    LABELS = ["anger", "fear", "joy", "sadness", "surprise"]
    MODEL_NAME = "microsoft/deberta-v3-base"
    MAX_LEN = 128
    BATCH_SIZE = 16
    EPOCHS = 4
    LR = 1.5e-5
    WEIGHT_DECAY = 0.01
    WARMUP_RATIO = 0.1
    N_FOLDS = 5
    TRAIN_CSV = "/kaggle/input/2025-sep-dl-gen-ai-project/train.csv"
    TEST_CSV = "/kaggle/input/2025-sep-dl-gen-ai-project/test.csv"
    SUBMISSION_PATH = "submission.csv"

CONFIG = Config()

## 3. Seed & Device Setup

**Reproducibility**: Setting seeds ensures that our results can be replicated exactly.
We set seeds for:
- NumPy random number generation
- PyTorch CPU operations
- PyTorch GPU operations (all CUDA devices)
- Python's built-in hash function

**Device Selection**: Automatically detects and uses GPU if available (CUDA), otherwise falls back to CPU.
GPU training is significantly faster (~10-50x) than CPU for deep learning models.

In [ ]:
def set_seed(seed=CONFIG.SEED):
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)

set_seed()

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

## 4. Utility Functions

Helper functions used throughout the pipeline:

### `ensure_text_column(df)`
- Standardizes the text column name across different datasets
- Searches for common alternatives like 'comment_text', 'sentence', etc.
- Raises error if no text column is found

### `tune_thresholds(y_true, y_prob)`
- **Critical for multi-label classification performance**
- Default threshold of 0.5 is often suboptimal
- Finds the best threshold per label that maximizes F1 score
- Tests 17 different thresholds between 0.1 and 0.9
- Can improve F1 score by 2-5% over default threshold

### `get_optimizer_params(model, lr, weight_decay)`
- Implements **differential weight decay**
- Applies weight decay to most parameters (helps prevent overfitting)
- No weight decay for bias and LayerNorm parameters (standard practice in transformer fine-tuning)
- This technique is recommended in the BERT and DeBERTa papers

In [ ]:
def ensure_text_column(df: pd.DataFrame) -> pd.DataFrame:
    if "text" in df.columns:
        return df
    for c in ["comment_text", "sentence", "content", "review"]:
        if c in df.columns:
            return df.rename(columns={c: "text"})
    raise ValueError("No text column found. Add/rename your text column to 'text'.")

def tune_thresholds(y_true: np.ndarray, y_prob: np.ndarray) -> np.ndarray:
    th = np.zeros(y_true.shape[1], dtype=np.float32)
    for j in range(y_true.shape[1]):
        best_t, best_f1 = 0.5, -1
        for t in np.linspace(0.1, 0.9, 17):
            f1 = f1_score(y_true[:, j], (y_prob[:, j] >= t).astype(int), zero_division=0)
            if f1 > best_f1:
                best_f1, best_t = f1, t
        th[j] = best_t
    return th

def get_optimizer_params(model, lr, weight_decay):
    param_optimizer = list(model.named_parameters())
    no_decay = ["bias", "LayerNorm.bias", "LayerNorm.weight"]
    optimizer_parameters = [
        {
            "params": [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)],
            "weight_decay": weight_decay,
        },
        {
            "params": [p for n, p in param_optimizer if any(nd in n for nd in no_decay)],
            "weight_decay": 0.0,
        },
    ]
    return optimizer_parameters

## 5. Dataset Class

Custom PyTorch Dataset for emotion classification.

**Key Features:**
- Tokenizes text on-the-fly using the DeBERTa tokenizer
- Handles both training data (with labels) and test data (without labels)
- Uses `padding='max_length'` to ensure all sequences have the same length (required for batching)
- Applies `truncation=True` to handle texts longer than MAX_LEN

**Returns:**
- `input_ids`: Token IDs representing the text
- `attention_mask`: Indicates which tokens are real vs padding
- `labels`: Multi-label binary targets (only for training data)

**PyTorch DataLoader** will use this dataset to create batches efficiently with multi-processing.

In [ ]:
class EmotionDS(torch.utils.data.Dataset):
    def __init__(self, df, tokenizer, max_len, is_test=False):
        self.texts = df["text"].tolist()
        self.is_test = is_test
        if not is_test:
            self.labels = df[CONFIG.LABELS].values.astype(np.float32)
        self.tok = tokenizer
        self.max_len = max_len

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, i):
        enc = self.tok(
            self.texts[i],
            truncation=True,
            padding="max_length",
            max_length=self.max_len,
            return_tensors="pt",
        )
        item = {k: v.squeeze(0) for k, v in enc.items()}
        if not self.is_test:
            item["labels"] = torch.tensor(self.labels[i])
        return item

## 6. Training & Validation Helper Functions

Core training and validation loops.

### `train_one_epoch()`
Trains the model for one complete pass through the training data.

**Key Techniques:**
- **Mixed Precision Training** (`autocast`): Uses float16 where safe, reducing memory and increasing speed by ~2x
- **Gradient Scaling** (`GradScaler`): Prevents gradient underflow in mixed precision
- **Gradient Clipping** (max_norm=1.0): Prevents exploding gradients, stabilizes training
- **Memory Efficient**: Uses `zero_grad(set_to_none=True)` and `non_blocking=True` for async GPU transfers

### `validate()`
Evaluates the model on validation data without updating weights.

**Features:**
- Runs in `model.eval()` mode (disables dropout, fixes batch normalization)
- Uses `torch.no_grad()` to save memory (no gradient computation)
- Applies sigmoid to convert logits to probabilities [0, 1]
- Returns predictions and targets for metric calculation

In [ ]:
def train_one_epoch(model, loader, optimizer, scheduler, scaler, criterion):
    model.train()
    losses = []
    for batch in loader:
        batch = {k: v.to(device, non_blocking=True) for k, v in batch.items()}
        optimizer.zero_grad(set_to_none=True)
        with autocast(enabled=True):
            out = model(input_ids=batch["input_ids"], attention_mask=batch["attention_mask"])
            loss = criterion(out.logits, batch["labels"])
        
        scaler.scale(loss).backward()
        scaler.unscale_(optimizer)
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        scaler.step(optimizer)
        scaler.update()
        scheduler.step()
        losses.append(loss.item())
    return np.mean(losses)

def validate(model, loader, criterion):
    model.eval()
    losses = []
    preds = []
    targs = []
    with torch.no_grad():
        for batch in loader:
            batch = {k: v.to(device, non_blocking=True) for k, v in batch.items()}
            with autocast(enabled=True):
                out = model(input_ids=batch["input_ids"], attention_mask=batch["attention_mask"])
                loss = criterion(out.logits, batch["labels"])
            losses.append(loss.item())
            preds.append(torch.sigmoid(out.logits).float().cpu().numpy())
            targs.append(batch["labels"].cpu().numpy())
    
    return np.mean(losses), np.vstack(preds), np.vstack(targs)

## 7. Main K-Fold Training Loop

The heart of our training pipeline - implements **5-Fold Stratified Cross-Validation**.

### Why K-Fold Cross-Validation?
- More reliable performance estimates than a single train/val split
- Every sample is used for validation exactly once
- Out-of-fold predictions can be used for threshold optimization
- Reduces variance in model performance

### Why Stratified?
- Maintains label distribution in each fold
- Important for imbalanced datasets
- For multi-label, we concatenate all labels into a string for stratification

### Training Process per Fold:
1. **Split data**: 80% training, 20% validation
2. **Initialize model**: Fresh DeBERTa-v3-base with random classification head
3. **Setup optimizer**: AdamW with differential weight decay
4. **Setup scheduler**: Linear warmup (10% of steps) then linear decay to 0
5. **Train for 4 epochs**: Track training and validation metrics
6. **Save best model**: Based on validation F1 score
7. **Store OOF predictions**: For threshold tuning
8. **Clean up memory**: Delete model and optimizer, run garbage collection

### Output:
- 5 trained models (one per fold) saved as `model_fold_{0-4}.pth`
- Out-of-fold predictions for the entire training set
- Cross-validated performance metrics

In [ ]:
def run_training():
    if not os.path.exists(CONFIG.TRAIN_CSV):
        print("Train CSV not found. Please check the path.")
        return None, None

    df = pd.read_csv(CONFIG.TRAIN_CSV)
    df = ensure_text_column(df)
    
    # Create Stratified Folds
    skf = StratifiedKFold(n_splits=CONFIG.N_FOLDS, shuffle=True, random_state=CONFIG.SEED)
    y_str = df[CONFIG.LABELS].astype(str).agg("".join, axis=1)
    
    oof_preds = np.zeros((len(df), len(CONFIG.LABELS)))
    
    tokenizer = AutoTokenizer.from_pretrained(CONFIG.MODEL_NAME)
    
    for fold, (train_idx, val_idx) in enumerate(skf.split(df, y_str)):
        print(f"\n{'='*20} FOLD {fold+1}/{CONFIG.N_FOLDS} {'='*20}")
        
        df_tr = df.iloc[train_idx].reset_index(drop=True)
        df_va = df.iloc[val_idx].reset_index(drop=True)
        
        ds_tr = EmotionDS(df_tr, tokenizer, CONFIG.MAX_LEN)
        ds_va = EmotionDS(df_va, tokenizer, CONFIG.MAX_LEN)
        
        dl_tr = torch.utils.data.DataLoader(ds_tr, batch_size=CONFIG.BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        dl_va = torch.utils.data.DataLoader(ds_va, batch_size=CONFIG.BATCH_SIZE, shuffle=False, num_workers=2, pin_memory=True)
        
        model = AutoModelForSequenceClassification.from_pretrained(
            CONFIG.MODEL_NAME, 
            num_labels=len(CONFIG.LABELS),
            problem_type="multi_label_classification"
        )
        model.to(device)
        
        optimizer_params = get_optimizer_params(model, CONFIG.LR, CONFIG.WEIGHT_DECAY)
        optimizer = AdamW(optimizer_params, lr=CONFIG.LR)
        
        total_steps = len(dl_tr) * CONFIG.EPOCHS
        scheduler = get_linear_schedule_with_warmup(
            optimizer, 
            num_warmup_steps=int(total_steps * CONFIG.WARMUP_RATIO), 
            num_training_steps=total_steps
        )
        
        criterion = nn.BCEWithLogitsLoss()
        scaler = GradScaler(enabled=True)
        
        best_f1 = 0
        best_state = None
        
        for ep in range(CONFIG.EPOCHS):
            train_loss = train_one_epoch(model, dl_tr, optimizer, scheduler, scaler, criterion)
            val_loss, val_preds, val_targs = validate(model, dl_va, criterion)
            
            val_f1 = f1_score(val_targs, (val_preds >= 0.5).astype(int), average="macro", zero_division=0)
            
            print(f"Ep {ep+1}: TrLoss={train_loss:.4f} | VaLoss={val_loss:.4f} | VaF1={val_f1:.4f}")
            
            if val_f1 > best_f1:
                best_f1 = val_f1
                best_state = model.state_dict()
                
        torch.save(best_state, f"model_fold_{fold}.pth")
        
        model.load_state_dict(best_state)
        _, val_preds, _ = validate(model, dl_va, criterion)
        oof_preds[val_idx] = val_preds
        
        del model, optimizer, scaler, scheduler
        torch.cuda.empty_cache()
        gc.collect()
        
    return oof_preds, df[CONFIG.LABELS].values

if os.path.exists(CONFIG.TRAIN_CSV):
    oof_preds, y_true = run_training()
else:
    print("Skipping training as data is not found (likely in a dry-run environment).")

## 8. Threshold Optimization

**Why optimize thresholds?**

In multi-label classification, we convert probabilities to binary predictions using a threshold:
- `prediction = 1 if probability >= threshold else 0`
- The default threshold of 0.5 is often suboptimal
- Different emotion labels may have different optimal thresholds

**Example:**
- 'Joy' might be common → optimal threshold could be 0.4
- 'Surprise' might be rare → optimal threshold could be 0.6

### Process:
1. Use out-of-fold predictions (already trained models, no data leakage)
2. For each label independently, test thresholds from 0.1 to 0.9
3. Select threshold that maximizes F1 score for that label
4. Apply optimized thresholds to get final binary predictions

**Expected Improvement**: 2-5% increase in Macro F1 score

This is a standard technique in Kaggle competitions and production systems.

In [ ]:
if os.path.exists(CONFIG.TRAIN_CSV):
    best_thresholds = tune_thresholds(y_true, oof_preds)
    oof_tuned = (oof_preds >= best_thresholds).astype(int)
    final_f1 = f1_score(y_true, oof_tuned, average="macro", zero_division=0)
    print(f"\nFinal CV Macro F1: {final_f1:.4f}")
    print(f"Best Thresholds: {best_thresholds}")
else:
    best_thresholds = np.array([0.5] * len(CONFIG.LABELS))

## 9. Inference & Submission

Final prediction pipeline for test data.

### Ensemble Strategy:
We use **model averaging** across all 5 folds:
1. Load each trained fold model
2. Make predictions on test set
3. Average the probabilities across all folds
4. Apply optimized thresholds to get binary predictions

### Why ensemble?
- Reduces variance and overfitting
- More robust predictions
- Often improves score by 1-3%
- Each fold sees different training data, captures different patterns

### Process:
1. Load test data and tokenize
2. For each fold:
   - Load saved model weights
   - Generate predictions (probabilities)
   - Clean up memory
3. Average all fold predictions
4. Apply optimized thresholds
5. Create submission file with format: `id, anger, fear, joy, sadness, surprise`

### Output:
- `submission.csv` ready for Kaggle upload
- Binary predictions (0 or 1) for each emotion per text

In [ ]:
def predict_test(thresholds):
    if not os.path.exists(CONFIG.TEST_CSV):
        print("Test CSV not found.")
        return

    df_test = pd.read_csv(CONFIG.TEST_CSV)
    df_test = ensure_text_column(df_test)
    
    tokenizer = AutoTokenizer.from_pretrained(CONFIG.MODEL_NAME)
    ds_test = EmotionDS(df_test, tokenizer, CONFIG.MAX_LEN, is_test=True)
    dl_test = torch.utils.data.DataLoader(ds_test, batch_size=CONFIG.BATCH_SIZE, shuffle=False, num_workers=2)
    
    fold_preds = []
    
    for fold in range(CONFIG.N_FOLDS):
        model_path = f"model_fold_{fold}.pth"
        if not os.path.exists(model_path):
            print(f"Model for fold {fold} not found, skipping.")
            continue
            
        print(f"Predicting Fold {fold+1}...")
        model = AutoModelForSequenceClassification.from_pretrained(
            CONFIG.MODEL_NAME, 
            num_labels=len(CONFIG.LABELS),
            problem_type="multi_label_classification"
        )
        model.load_state_dict(torch.load(model_path))
        model.to(device)
        model.eval()
        
        preds = []
        with torch.no_grad():
            for batch in dl_test:
                batch = {k: v.to(device, non_blocking=True) for k, v in batch.items()}
                with autocast(enabled=True):
                    out = model(input_ids=batch["input_ids"], attention_mask=batch["attention_mask"])
                preds.append(torch.sigmoid(out.logits).float().cpu().numpy())
        
        fold_preds.append(np.vstack(preds))
        del model
        torch.cuda.empty_cache()
        gc.collect()
        
    if not fold_preds:
        print("No predictions made.")
        return

    avg_preds = np.mean(fold_preds, axis=0)
    final_preds = (avg_preds >= thresholds).astype(int)
    
    sub = pd.DataFrame(columns=["id"] + CONFIG.LABELS)
    sub["id"] = df_test["id"] if "id" in df_test.columns else np.arange(len(df_test))
    sub[CONFIG.LABELS] = final_preds
    sub.to_csv(CONFIG.SUBMISSION_PATH, index=False)
    print(f"Submission saved to {CONFIG.SUBMISSION_PATH}")
    print(sub.head())

predict_test(best_thresholds)